<a href="https://colab.research.google.com/github/MariaFekry/E_Library/blob/master/GPU_T1_trans_change.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import shutil

In [ ]:
shutil.rmtree('SuperGlobal', ignore_errors=True)

In [ ]:
!git clone https://github.com/ShihaoShao-GH/SuperGlobal.git

Cloning into 'SuperGlobal'...
remote: Enumerating objects: 143, done.
remote: Counting objects: 100% (37/37), done.
remote: Compressing objects: 100% (35/35), done.
remote: Total 143 (delta 7), reused 2 (delta 2), pack-reused 106 (from 1)
Receiving objects: 100% (143/143), 12.56 MiB | 23.78 MiB/s, done.
Resolving deltas: 100% (44/44), done.


In [ ]:
!mkdir -p ./weights

In [ ]:
!gdown "https://drive.google.com/uc?id=11AqMHiaIf0dhCLhWyLZ5ZNY5I42NTAH8" -O ./weights/CVPR2022_CVNet_R101.pyth


Downloading...
From (original): https://drive.google.com/uc?id=11AqMHiaIf0dhCLhWyLZ5ZNY5I42NTAH8
From (redirected): https://drive.google.com/uc?id=11AqMHiaIf0dhCLhWyLZ5ZNY5I42NTAH8&confirm=t&uuid=e42c4c0d-d4c3-456a-b870-67fab31066a6
To: /content/weights/CVPR2022_CVNet_R101.pyth
100% 217M/217M [00:01<00:00, 115MB/s] 


In [ ]:
from google.colab import drive
import os
import pandas as pd
from PIL import Image
import torch
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms
from SuperGlobal.model.CVNet_Rerank_model import CVNet_Rerank
from SuperGlobal.modules.coarse_retrieval.gemp import gemp
from SuperGlobal.modules.coarse_retrieval.rgem import rgem
from SuperGlobal.modules.coarse_retrieval.sgem import sgem
import torch.nn.functional as F


In [ ]:
# Step 1: Mount Google Drive
drive.mount('/content/drive')

# Step 2: Set Paths
drive_base_path = "/content/drive/MyDrive/GP"
train_csv = os.path.join(drive_base_path, "train_monument.csv")
val_csv = os.path.join(drive_base_path, "valid_monuments.csv")
test_csv = os.path.join(drive_base_path, "test_monuments.csv")
train_folder = os.path.join(drive_base_path, "train images")
val_folder = os.path.join(drive_base_path, "valid images")
test_folder = os.path.join(drive_base_path, "test images")

# Step 3: Create Class-to-Index Mapping Dynamically
def create_class_to_idx(csv_file):
    data = pd.read_csv(csv_file)
    unique_classes = sorted(data['class'].unique())  # Get unique class names
    class_to_idx = {cls_name: idx for idx, cls_name in enumerate(unique_classes)}  # Map class to index
    return class_to_idx

# Dynamically create mapping using the training data
class_to_idx = create_class_to_idx(train_csv)
print("Class-to-Index Mapping:", class_to_idx)  # Optional: Check mapping

# Step 4: Define the Custom Dataset
class CVNetDataset(Dataset):
    def __init__(self, csv_file, images_folder, transform=None, class_to_idx=None):
        self.data = pd.read_csv(csv_file)
        self.images_folder = images_folder
        self.transform = transform
        self.class_to_idx = class_to_idx

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        # Get image name and label
        image_name = self.data.iloc[idx]['filename']
        label = self.data.iloc[idx]['class']

        # Load the image
        image_path = os.path.join(self.images_folder, image_name)
        image = Image.open(image_path).convert("RGB")  # Ensure 3 channels

        # Apply transformations to the image
        if self.transform:
            image = self.transform(image)

        # Map label to integer using class_to_idx
        label = self.class_to_idx[label]
        label = torch.tensor(label, dtype=torch.long)

        return image, label, image_name  # Return image, label, and filename

# Step 5: Define initial Transformations
initial_transform = transforms.Compose([
    transforms.Resize((512, 512)),  # Resize images to the size expected by the model
    transforms.ToTensor(),          # Convert to tensor

])

temp_dataset = CVNetDataset(train_csv, train_folder, transform=initial_transform, class_to_idx=class_to_idx)




Mounted at /content/drive
Class-to-Index Mapping: {'Akhenaten': 0, 'Bent-pyramid-for-senefru': 1, 'Colossal-Statue-of-Ramesses-II': 2, 'Colossoi-of-Memnon': 3, 'Goddess-Isis-with-her-child': 4, 'Hatshepsut': 5, 'Hatshepsut-face': 6, 'Khafre-Pyramid': 7, 'Mask-of-Tutankhamun': 8, 'Nefertiti': 9, 'Pyramid_of_Djoser': 10, 'Ramessum': 11, 'Ramses-II-Red-Granite-Statue': 12, 'Statue-of-King-Zoser': 13, 'Statue-of-Tutankhamun-with-Ankhesenamun': 14, 'Temple_of_Isis_in_Philae': 15, 'Temple_of_Kom_Ombo': 16, 'The Great Temple of Ramesses -': 17, 'amenhotep-iii-and-tiye': 18, 'bust-of-ramesses-ii': 19, 'menkaure-pyramid': 20, 'sphinx': 21}


In [ ]:
def get_dataset_stats(train_dataset):
    print("Calculating dataset statistics...")
    # Create temporary loader without normalization
    temp_loader = DataLoader(train_dataset, batch_size=32, num_workers=0, shuffle=False)

    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using device: {device}")

    mean = 0.
    std = 0.
    total_images = 0

    for images, _, _ in temp_loader:  # Note the _ for label and image_name
        images = images.to(device)
        batch_samples = images.size(0)
        images = images.view(batch_samples, images.size(1), -1)
        mean += images.mean(2).sum(0)
        std += images.std(2).sum(0)
        total_images += batch_samples

    mean /= total_images
    std /= total_images

    print(f"Dataset mean: {mean}")
    print(f"Dataset std: {std}")
    return mean, std

In [ ]:
mean,std = get_dataset_stats(temp_dataset)
adjusted_std = std * 1.2
# Step 6: Create final transform with calculated mean and std
transform = transforms.Compose([
    transforms.Resize((512, 512)),
    transforms.CenterCrop(448),
    transforms.ToTensor(),
    transforms.Normalize(mean=mean.tolist(), std=adjusted_std.tolist())
])

train_dataset = CVNetDataset(train_csv, train_folder, transform=transform, class_to_idx=class_to_idx)
val_dataset = CVNetDataset(val_csv, val_folder, transform=transform, class_to_idx=class_to_idx)
test_dataset = CVNetDataset(test_csv, test_folder, transform=transform, class_to_idx=class_to_idx)

# Step 7: Create DataLoaders
batch_size = 32
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)

Calculating dataset statistics...
Using device: cuda
Dataset mean: tensor([0.5454, 0.5148, 0.4818], device='cuda:0')
Dataset std: tensor([0.2057, 0.1931, 0.2158], device='cuda:0')


In [ ]:
def verify_normalization(dataset):
    # Get a sample batch
    loader = DataLoader(dataset, batch_size=32, shuffle=True)
    images, _, _ = next(iter(loader))

    # Check mean and std
    batch_mean = images.mean(dim=[0, 2, 3])
    batch_std = images.std(dim=[0, 2, 3])

    print("Verification:")
    print(f"Batch mean: {batch_mean}")  # Should be close to 0
    print(f"Batch std: {batch_std}")    # Should be close to 1

# Verify normalization
verify_normalization(train_dataset)

Verification:
Batch mean: tensor([ 0.0139, -0.0313, -0.0388])
Batch std: tensor([0.9545, 0.9804, 0.9572])


In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
def setup_cvnet():
    # Initialize the model components
    model = CVNet_Rerank(RESNET_DEPTH=101, REDUCTION_DIM=2048, relup=True)
    Gemp = gemp()
    Rgem = rgem()
    Sgem = sgem()

    # Load pre-trained weights
    checkpoint = torch.load('/content/weights/CVPR2022_CVNet_R101.pyth', map_location='cuda' if torch.cuda.is_available() else 'cpu')
    model_state = model.state_dict()
    pretrained_state = checkpoint['model_state']

    missing_keys, unexpected_keys = model.load_state_dict(pretrained_state, strict=False)
    # Print any mismatched keys
    if missing_keys:
        print("⚠️ Missing keys (these layers are in the model but not in the checkpoint):")
        print(missing_keys)
    if unexpected_keys:
        print("⚠️ Unexpected keys (these layers are in the checkpoint but not in the model):")
        print(unexpected_keys)

    return model, Gemp, Rgem, Sgem

def calculate_ap(ranked_labels, true_label):
    """
    Calculate Average Precision for a single query

    Args:
        ranked_labels: List of class labels for retrieved images, ordered by similarity
        true_label: The true class label of the query image
    """
    relevant_positions = [i + 1 for i, label in enumerate(ranked_labels) if label == true_label]
    if not relevant_positions:
        return 0.0

    precision_values = []
    for i, position in enumerate(relevant_positions, 1):
        precision = i / position
        precision_values.append(precision)

    return sum(precision_values) / len(precision_values)

def extract_features_and_save(model, loader, gemp, rgem, sgem, device, save_path):
    model.eval()
    features = {}
    labels = {}
    scale_list = 3

    os.makedirs(save_path, exist_ok=True)

    with torch.no_grad():
        for batch in loader:
            images, label_indices, image_names = batch
            images = images.to(device)

            batch_features = model.extract_global_descriptor(images, gemp, rgem, sgem, scale_list)

            if not isinstance(batch_features, list):
                batch_features = F.normalize(batch_features, p=2, dim=1)
            else:
                batch_features = [F.normalize(feat, p=2, dim=1) for feat in batch_features]
                stacked_features = torch.stack(batch_features, dim=0)
                batch_features = torch.mean(stacked_features, dim=0)
                batch_features = F.normalize(batch_features, p=2, dim=1)

            # Store features as tensors, not numpy arrays
            for idx, name in enumerate(image_names):
                features[name] = batch_features[idx].cpu().clone()  # Keep as tensor
                labels[name] = label_indices[idx].item()

    # Save features and labels as dictionaries of tensors
    torch.save({'features': features, 'labels': labels}, os.path.join(save_path, 'features_and_labels.pth'))
    print(f"Features and labels saved to {save_path}")
    return features, labels

def load_saved_features(save_path):
    features_path = os.path.join(save_path, 'features_and_labels.pth')

    if os.path.exists(features_path):
        saved_data = torch.load(features_path)
        features = saved_data['features']
        labels = saved_data['labels']
        print(f"Loaded saved features and labels from {save_path}")
        return features, labels
    else:
        print(f"No saved features found at {save_path}")
        return None, None

def evaluate_map(model, test_loader, database_features, database_labels, gemp, rgem, sgem, device,k=10):
    model.eval()
    aps = []
    total_processed = 0

    try:
        with torch.no_grad():
            for batch_idx, (images, labels, image_names) in enumerate(test_loader):
                print(f"\nProcessing batch {batch_idx + 1}/{len(test_loader)}")
                print(f"Batch size: {len(images)}")

                images = images.to(device)
                query_features = model.extract_global_descriptor(images, gemp, rgem, sgem, scale_list=3)

                if isinstance(query_features, list):
                    print("features are multiple scales\n")
                    query_features = [F.normalize(feat, p=2, dim=1) for feat in query_features]
                    query_features = torch.mean(torch.stack(query_features, dim=0), dim=0)
                    query_features = F.normalize(query_features, p=2, dim=1)
                else:
                    query_features = F.normalize(query_features, p=2, dim=1)

                for idx, query_feature in enumerate(query_features):
                    query_label = labels[idx].item()
                    similarities = {}
                    print(f"query lable is {query_label}\n")

                    # Calculate similarities with database features
                    for db_name, db_feat in database_features.items():
                        # Ensure database feature is a tensor and on the correct device
                        db_feat = db_feat.to(device)

                        # Calculate similarity
                        similarity = torch.dot(query_feature, db_feat) / (
                            query_feature.norm() * db_feat.norm()
                        )
                        similarities[db_name] = (similarity.item(), database_labels[db_name])

                    ranked_results = sorted(similarities.items(), key=lambda x: x[1][0], reverse=True)[:k]
                    ranked_labels = [label for _, (_, label) in ranked_results]
                    print(f" Top {k} Ranked labels: {ranked_labels}\n")

                    ap = calculate_ap(ranked_labels, query_label)
                    aps.append(ap)
                    total_processed += 1

                print(f"Processed {total_processed} images so far")
                print(f"Current running mAP: {sum(aps)/len(aps):.4f}")

    except Exception as e:
        print(f"\nError encountered: {str(e)}")
        import traceback
        traceback.print_exc()

    finally:
        if aps:
            map_score = sum(aps) / len(aps)
            print(f"\nProcessed {total_processed} images in total")
            return map_score, aps
        else:
            return 0.0, []

def main():
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using device: {device}")

    # Setup Model
    model, gemp, rgem, sgem = setup_cvnet()
    model = model.to(device)

    save_path = "/content/drive/MyDrive/GP2/features"

    # Load or extract database features
    database_features, database_labels = load_saved_features(save_path)
    if database_features is None or database_labels is None:
        print("Extracting database features...")
        database_features, database_labels = extract_features_and_save(
            model, train_loader, gemp, rgem, sgem, device, save_path
        )

    print(f"Number of database images: {len(database_features)}")

    # Calculate mAP
    print("\nCalculating mAP...")
    topk=5
    map_score, aps = evaluate_map(
        model, test_loader, database_features, database_labels,
        gemp, rgem, sgem, device,topk
    )

    # Print and save results
    print(f"\nFinal Results:")
    print(f"mAP: {map_score:.4f}")
    print(f"Min AP: {min(aps):.4f}")
    print(f"Max AP: {max(aps):.4f}")
    print(f"Median AP: {sorted(aps)[len(aps)//2]:.4f}")

if __name__ == "__main__":
    main()

Using device: cuda


<ipython-input-13-4007d9e1eb28>:9: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load('/content/weights/CVPR2022_CVNet_R101.pyth', map_location='cuda' if 

⚠️ Missing keys (these layers are in the model but not in the checkpoint):
['encoder_q.seb1.weight', 'encoder_q.seb1.bias', 'encoder_q.seb2.weight', 'encoder_q.seb2.bias', 'encoder_q.sefc.weight', 'encoder_q.sefc.bias']
No saved features found at /content/drive/MyDrive/GP2/features
Extracting database features...
Features and labels saved to /content/drive/MyDrive/GP2/features
Number of database images: 2066

Calculating mAP...

Processing batch 1/19
Batch size: 32
query lable is 11

Ranked labels: [11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 16, 11, 11, 11, 11, 11, 11, 16, 11, 11, 11, 11, 11, 11, 11, 11, 11, 16, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 11, 16, 11, 11, 11, 11, 11, 16, 11, 16, 11, 16, 11, 16, 11, 16, 11, 11, 16, 16, 11, 16, 11, 2, 11, 11, 16, 11, 17, 11, 11, 11, 17, 11, 11, 16, 17, 3, 12, 11, 11, 2, 17, 2, 16, 16, 2, 3, 16, 2, 12, 12